In [35]:
# Install necessary packages
!pip install selenium
!pip install webdriver-manager

In [36]:
# Starts here

In [37]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import Select
from selenium.common.exceptions import TimeoutException
from selenium.common.exceptions import (
    NoSuchElementException,
    TimeoutException,
    StaleElementReferenceException,
    ElementClickInterceptedException,
    WebDriverException,
    UnexpectedTagNameException # For Select issues
)

import pandas as pd
import threading
import queue
import re
import time
import random
import traceback

In [38]:
def reinitialize_driver():
    """Completely reinitialize the WebDriver"""
    global driver
    
    print("Initializing WebDriver...")
    
    try:
        # Quit existing driver if it exists
        if driver is not None:
            driver.quit()
    except:
        print("Error closing existing driver")
    
    # Set up Chrome options with better memory management
    options = webdriver.ChromeOptions()
    options.add_argument('--headless')
    options.add_argument('--no-sandbox')
    options.add_argument('--disable-dev-shm-usage')
    options.add_argument('--disable-gpu')
    options.add_argument('--disable-extensions')
    
    # For Mac environment, use webdriver_manager to handle ChromeDriver
    from webdriver_manager.chrome import ChromeDriverManager
    from selenium.webdriver.chrome.service import Service
    
    # Initialize a new driver
    service = Service(ChromeDriverManager().install())
    driver = webdriver.Chrome(service=service, options=options)
    
    # Set shorter timeouts
    driver.set_page_load_timeout(30)
    driver.implicitly_wait(10)
    
    return driver

In [43]:
def navigate_to_website(url):
    """Navigate to the target website"""
    driver.get(url)
    time.sleep(3)
    print(f"Successfully navigated to {url}")
    print(f"Page title: {driver.title}")

In [45]:
def fill_and_submit_form(form_values):
    """Fill the form with specified values and submit it"""
    print("Filling form with values:", form_values)

    # Handle mudda_type first to trigger dependent dropdown
    if "mudda_type" in form_values:
        mudda_type_select = Select(driver.find_element(By.ID, "mudda_type"))
        mudda_type_select.select_by_value(form_values["mudda_type"])
        time.sleep(2)  # Wait for dependent dropdown to update

    # Fill all other form fields
    for field_name, value in form_values.items():
        if field_name == "mudda_type":
            continue  # Already handled

        try:
            element = driver.find_element(By.NAME, field_name)
            if element.tag_name == "select":
                select = Select(element)
                select.select_by_value(str(value))
                print(f"Selected '{value}' for dropdown '{field_name}'")
            else:
                element.clear()
                element.send_keys(value)
                print(f"Filled input field '{field_name}' with '{value}'")
        except Exception as e:
            print(f"Error filling field '{field_name}': {e}")

    # Submit the form
    try:
        submit_button = driver.find_element(By.CSS_SELECTOR, "input[name='Submit'][type='submit']")
        submit_button.click()
        print("Form submitted successfully")
        time.sleep(5)  # Wait for results to load
    except Exception as e:
        print(f"Error submitting form: {e}")

In [71]:
def has_next_page(driver):
    """Check if there's a next page link ('»') with error logging."""
    try:
        # Wait briefly for pagination to potentially appear/update
        WebDriverWait(driver, 5).until(
            EC.presence_of_element_located((By.ID, "pagination"))
        )
        pagination = driver.find_element(By.ID, "pagination")
        # Specifically look for the '»' link which indicates a next page
        next_links = pagination.find_elements(By.XPATH, ".//a[text()='»']")
        return len(next_links) > 0
    except (NoSuchElementException, TimeoutException):
        # If pagination element or link isn't found after waiting, assume no next page
        # safe_print("Pagination or next link ('»') not found.") # Can be noisy
        return False
    except StaleElementReferenceException:
        safe_print("Stale element reference when checking for next page.")
        return False # Can't determine if stale
    except Exception as e:
        safe_print(f"Unexpected error checking for next page: {type(e).__name__} - {e}")
        return False

def go_to_next_page(driver):
    """Navigate to the next page using the '»' link with error logging and pre-click wait."""
    try:
        # Wait specifically for the pagination element AND the next link to be clickable
        pagination = WebDriverWait(driver, 15).until(
            EC.presence_of_element_located((By.ID, "pagination"))
        )
        next_link = WebDriverWait(pagination, 15).until(
             EC.element_to_be_clickable((By.XPATH, ".//a[text()='»']"))
        )
        # safe_print("Next link found and clickable.") # Optional debug msg
        next_link.click()
        # The wait for the *new* page's content should happen in the *caller* (process_combination)
        # A minimal sleep might help ensure the click registers before the caller starts waiting.
        time.sleep(1)
        return True
    except (NoSuchElementException, TimeoutException, ElementClickInterceptedException, StaleElementReferenceException) as e:
        safe_print(f"Error clicking next page link: {type(e).__name__} - {e}")
        return False
    except Exception as e:
        safe_print(f"Unexpected error going to next page: {type(e).__name__} - {e}")
        return False

In [49]:
def extract_search_results(driver):
    """Extract search results with proper selectors and error logging."""
    results = []
    try:
        # Look for articles
        articles = driver.find_elements(By.XPATH, "//article[contains(@class, 'format-standard')]")

        if not articles:
            # It's possible to have a results page with no actual results listed
            # safe_print(f"No article elements found on current page: {driver.current_url}")
            return [] # Return empty list, not necessarily an error

        for article in articles:
            case_data = {}
            try:
                # Extract title and link
                title_link = article.find_element(By.XPATH, ".//h3[@class='post-title']/a")
                case_data["title"] = title_link.text.strip()
                case_data["link"] = title_link.get_attribute("href")

                # Extract ijlas name
                try:
                    ijlas_link = article.find_element(By.XPATH, ".//span[.//i[contains(@class, 'glyphicon-tag')]]/a")
                    case_data["ijlas_name"] = ijlas_link.text.strip()
                except NoSuchElementException:
                    # safe_print(f"  - Ijlas name not found for article.") # Optional: can be noisy
                    case_data["ijlas_name"] = ""

                # Add if valid
                if case_data.get("title") and case_data.get("link"):
                    results.append(case_data)
                else:
                    safe_print(f"  - Warning: Incomplete data extracted for an article (Title: {case_data.get('title')}, Link: {case_data.get('link')})")

            except NoSuchElementException as e:
                safe_print(f"  - Error extracting details from one article: {e}")
                continue # Skip this article, try the next
            except StaleElementReferenceException as e:
                safe_print(f"  - Stale element error extracting details from one article: {e}")
                continue # Skip this article, element detached from DOM
            except Exception as e:
                safe_print(f"  - Unexpected error extracting details from one article: {type(e).__name__} - {e}")
                continue # Skip this article

        return results

    except StaleElementReferenceException as e:
         safe_print(f"Error finding articles (StaleElement): {e} on page {driver.current_url}")
         return [] # Cannot process page if main container is stale
    except Exception as e:
        safe_print(f"Error finding article elements: {type(e).__name__} - {e} on page {driver.current_url}")
        return []

In [51]:
def save_to_csv(cases, filename):
    """Save case data to CSV file"""
    if not cases:
        print("No cases to save")
        return

    # Create a DataFrame
    df = pd.DataFrame(cases)

    # Save to CSV
    df.to_csv(filename, index=False, encoding='utf-8-sig')  # utf-8-sig for proper Nepali characters
    print(f"Saved {len(cases)} cases to {filename}")

In [53]:
def parse_mudda_mapping(mapping_text):
    """Parse the provided mapping text into a structured dictionary"""
    mapping = {}
    current_mudda_type = None

    for line in mapping_text.splitlines():
        line = line.strip()

        if "--- Mudda Type:" in line:
            # Extract mudda_type value
            value_match = re.search(r"\(Value: (\d+)\)", line)
            if value_match:
                current_mudda_type = value_match.group(1)
                mapping[current_mudda_type] = []

        elif "- Name:" in line and current_mudda_type:
            # Extract mudda_name value - try different pattern
            name_match = re.search(r"'(.+?)' \(Value: (\d+)\)", line)

            if name_match:
                name_text = name_match.group(1)
                name_value = name_match.group(2)

                # Skip value 385 as requested
                if name_value != "385":
                    mapping[current_mudda_type].append({
                        "value": name_value,
                        "text": name_text
                    })

    return mapping

In [55]:
mapping_text = """--- Mudda Type: 'दुनियाबादी देवानी' (Value: 1) ---
  - Name: '........' (Value: 385)
  - Name: 'अंश' (Value: 1)
  - Name: 'अंश जालसाजी' (Value: 314)
  - Name: 'अंशबन्डा' (Value: 186)
  - Name: 'अग्नि बिमा दाबी' (Value: 423)
  - Name: 'अधिकार पत्र बदर' (Value: 433)
  - Name: 'अनियमितता' (Value: 426)
  - Name: 'अपुताली' (Value: 2)
  - Name: 'अपुताली धनमाल' (Value: 300)
  - Name: 'अबन्डा जग्गा बन्डा' (Value: 419)
  - Name: 'अबन्डा धन बन्डा गराई पाउँ' (Value: 326)
  - Name: 'अर्को लिखत गराइपाऊँ' (Value: 404)
  - Name: 'अवैध रूपमा भवन निर्माण' (Value: 245)
  - Name: 'आदेश जारी गरी पाऊँ' (Value: 172)
  - Name: 'आदेश बदर' (Value: 207)
  - Name: 'आदेश बदर गरी हाजिर गराई पाउँ' (Value: 262)
  - Name: 'आम्दानी खर्च' (Value: 265)
  - Name: 'आयस्ता दिलाई पाऊँ' (Value: 305)
  - Name: 'आयस्ता वाली' (Value: 307)
  - Name: 'आर्य समाजी' (Value: 286)
  - Name: 'इन्साफ जाँच' (Value: 205)
  - Name: 'उखडा जग्गा' (Value: 391)
  - Name: 'उपयुक्त आदेश जारी गरी पाउँ' (Value: 258)
  - Name: 'क. ख. समेत' (Value: 241)
  - Name: 'कम्पनी सम्बन्धी' (Value: 192)
  - Name: 'करार' (Value: 3)
  - Name: 'कर्म थकाली' (Value: 388)
  - Name: 'कागज सच्यायो' (Value: 291)
  - Name: 'कित्ताकाट' (Value: 430)
  - Name: 'कित्ताकाट ट्रायल चेक' (Value: 411)
  - Name: 'किलास खिचोला' (Value: 359)
  - Name: 'किल्ला बदर' (Value: 347)
  - Name: 'कुत दिलाई मोही निष्काशन गरी पाउा' (Value: 253)
  - Name: 'कुत बाली' (Value: 343)
  - Name: 'कुलो पानी' (Value: 180)
  - Name: 'कुलो पानी' (Value: 4)
  - Name: 'क्षतिपुर्ति' (Value: 5)
  - Name: 'क्षेत्रफल सुधार' (Value: 226)
  - Name: 'खान लाउन दिलाई पाऊँ' (Value: 155)
  - Name: 'खानी लाइसेन्स बदर' (Value: 368)
  - Name: 'खिचोला' (Value: 324)
  - Name: 'खिचोला दर्ता बदर' (Value: 185)
  - Name: 'खिचोला पर्चा बदर गुठी' (Value: 178)
  - Name: 'खिचोला मेटाई' (Value: 215)
  - Name: 'खिचोला हक कायम' (Value: 195)
  - Name: 'गुठी सम्बन्धी' (Value: 6)
  - Name: 'गोश्वारा दर्ता कायम' (Value: 243)
  - Name: 'घर जग्गासम्बन्धी' (Value: 174)
  - Name: 'घर भत्काई पाऊँ' (Value: 330)
  - Name: 'घर भत्काई बाटो खुलाई' (Value: 315)
  - Name: 'घर भवन सम्बन्धी' (Value: 7)
  - Name: 'घरेलु हिंसा' (Value: 425)
  - Name: 'चलन चलाई पाऊँ' (Value: 217)
  - Name: 'चिकित्सकको रूपमा दर्ता गराइपाऊँ ।' (Value: 212)
  - Name: 'जग्गा खिचोला' (Value: 358)
  - Name: 'जग्गा जालसाजी' (Value: 313)
  - Name: 'जग्गा दर्ता नामसारी' (Value: 427)
  - Name: 'जग्गा निखनाई पाउँ' (Value: 320)
  - Name: 'जग्गा बाली' (Value: 282)
  - Name: 'जग्गा सम्बन्धी' (Value: 8)
  - Name: 'जातक मार्‍यो' (Value: 379)
  - Name: 'जायजात बेहिसाब' (Value: 304)
  - Name: 'जिउनी जग्गा' (Value: 325)
  - Name: 'जिमिदारी नामसारी' (Value: 269)
  - Name: 'जिरायत' (Value: 403)
  - Name: 'जोत कट्टा' (Value: 266)
  - Name: 'जोत कायम' (Value: 190)
  - Name: 'जोत बदर' (Value: 405)
  - Name: 'झुक्याई कागज गरायो' (Value: 290)
  - Name: 'टिकटको रूपैयाँ दिलाइ पाउँ' (Value: 382)
  - Name: 'ट्रेडमार्क दर्ता' (Value: 139)
  - Name: 'ट्रेडमार्क संशोधन' (Value: 420)
  - Name: 'ठेक्का रकम' (Value: 229)
  - Name: 'डाक रोकी पाउँ' (Value: 285)
  - Name: 'तलब दिलाई पाउँ' (Value: 376)
  - Name: 'तायदाती फैसला बदर' (Value: 322)
  - Name: 'तालुकी' (Value: 200)
  - Name: 'तिरो बुझाई पाऊँ' (Value: 309)
  - Name: 'थकाली लूय गरिपाऊँ' (Value: 339)
  - Name: 'थैली फिर्ता पाऊँ' (Value: 401)
  - Name: 'थैली बुझाई पाउँ' (Value: 275)
  - Name: 'दर्ता कायम' (Value: 247)
  - Name: 'दर्ता गरी पाउँ' (Value: 336)
  - Name: 'दर्ता बदर' (Value: 203)
  - Name: 'दर्ता बदर, नामसारी' (Value: 146)
  - Name: 'दाइजो पेवा' (Value: 383)
  - Name: 'दाखिल खारेज' (Value: 183)
  - Name: 'दामासाही गरिपाऊँ' (Value: 399)
  - Name: 'दुनियावादी देवानी विविध' (Value: 9)
  - Name: 'दूषित दर्ता' (Value: 191)
  - Name: 'दोहरा लिखत' (Value: 280)
  - Name: 'दोहोरो दर्ता श्रेस्ता' (Value: 255)
  - Name: 'धनमाल' (Value: 10)
  - Name: 'धरौट' (Value: 270)
  - Name: 'धर्मपुत्र / पुत्री' (Value: 11)
  - Name: 'धर्मपुत्र लिखत बदर' (Value: 169)
  - Name: 'धर्मलोप' (Value: 136)
  - Name: 'नक्सा पास' (Value: 393)
  - Name: 'नक्सा बेगर ढोका गोठ बनाएको भत्काई पाउँ' (Value: 346)
  - Name: 'नाता कायम' (Value: 259)
  - Name: 'नापी दर्ता बदर दर्ता' (Value: 161)
  - Name: 'नामसारी' (Value: 171)
  - Name: 'नासो धरौट' (Value: 199)
  - Name: 'निखनाई पाऊँ' (Value: 202)
  - Name: 'निर्णय दर्ता बदर' (Value: 213)
  - Name: 'निर्णय दर्ता बदर हक कायम दर्तासमेत' (Value: 141)
  - Name: 'निर्णय बदर समेत' (Value: 162)
  - Name: 'निर्वाचन' (Value: 12)
  - Name: 'निर्वाचन बदर' (Value: 210)
  - Name: 'निवेदन' (Value: 188)
  - Name: 'पदमा कायम' (Value: 345)
  - Name: 'पर्खाल खिचोला' (Value: 362)
  - Name: 'पर्खाल भत्काई सार्वजनिक कुलो कायम' (Value: 263)
  - Name: 'पर्चा बदर' (Value: 380)
  - Name: 'पर्वते रौजौटा कायम' (Value: 349)
  - Name: 'पसलबाट उठाई पाउँ' (Value: 335)
  - Name: 'पाल्ही भट्टि रकम' (Value: 297)
  - Name: 'पास गराई पाऊँ ।' (Value: 397)
  - Name: 'पास गराई पाऊँ ।' (Value: 398)
  - Name: 'पेटेन्ट ,डिजाइन,ट्रेडमार्क' (Value: 13)
  - Name: 'पैनी तोडी दियो' (Value: 377)
  - Name: 'पोत दिलाई पाऊँ' (Value: 308)
  - Name: 'फट्टा दिलाई पाउँ भन्ने' (Value: 396)
  - Name: 'फिल्डबुक सच्याएको दर्ता' (Value: 350)
  - Name: 'फैसला वदर' (Value: 14)
  - Name: 'बकस जग्गा' (Value: 316)
  - Name: 'बकसपत्र' (Value: 149)
  - Name: 'बच्चा जिम्मा लगाई पाउँ' (Value: 417)
  - Name: 'बन्डापत्र' (Value: 237)
  - Name: 'बन्धकी' (Value: 230)
  - Name: 'बन्धकी थैली' (Value: 296)
  - Name: 'बर्खास्ती बदर' (Value: 206)
  - Name: 'बहाल बुझाई पाउँ' (Value: 277)
  - Name: 'बहाल भराई पाउँ' (Value: 170)
  - Name: 'बाँध काट्यो' (Value: 332)
  - Name: 'बाटो खुलाई पाऊँ' (Value: 264)
  - Name: 'बालीसम्बन्धी' (Value: 181)
  - Name: 'बिक्री बदर' (Value: 182)
  - Name: 'बिक्रीकर निर्धारण' (Value: 361)
  - Name: 'बिगो असुल' (Value: 175)
  - Name: 'बिमा दाबी' (Value: 434)
  - Name: 'बेहिसावको नालिस खारेज' (Value: 311)
  - Name: 'बैक ग्यारेन्टी' (Value: 246)
  - Name: 'ब्याज भराई पाउँ' (Value: 244)
  - Name: 'भत्काई पाऊँ' (Value: 248)
  - Name: 'भरेङ बाटो कायम गरिपाऊँ ।' (Value: 168)
  - Name: 'भरेङ बाटो कायम गरिपाऊँ ।' (Value: 167)
  - Name: 'भाडा दिलाई घर खाली' (Value: 232)
  - Name: 'मध्यस्थता' (Value: 15)
  - Name: 'मानाचामल' (Value: 150)
  - Name: 'मिलापत्र' (Value: 16)
  - Name: 'मुद्दा सकार गरिपाऊँ' (Value: 351)
  - Name: 'मोही' (Value: 17)
  - Name: 'मोही निष्काशन' (Value: 254)
  - Name: 'म्याद तामेली' (Value: 221)
  - Name: 'रकम दिलाई भराई पाऊँ' (Value: 145)
  - Name: 'रसिद दिलाइ पाउँ' (Value: 408)
  - Name: 'राजिनामा दर्ता वदर हक कायम' (Value: 261)
  - Name: 'राजिनामा लिखत बदर' (Value: 159)
  - Name: 'राजिनामा सम्बन्धी' (Value: 354)
  - Name: 'राजीनामा खोसी झुक्याई सही गरायो' (Value: 353)
  - Name: 'रोक्का धनमाल हिनामिना' (Value: 374)
  - Name: 'रोक्का बदर' (Value: 239)
  - Name: 'रोक्का बाली फुकुवा पाउँ' (Value: 272)
  - Name: 'लगत सच्याई पाऊँ' (Value: 249)
  - Name: 'लिखत जालसाजी' (Value: 283)
  - Name: 'लिखत दर्ता बदर' (Value: 154)
  - Name: 'लिखत पारित' (Value: 193)
  - Name: 'लिखत पास' (Value: 337)
  - Name: 'लिखत फिर्ता पाउँ' (Value: 317)
  - Name: 'लिखत बदर' (Value: 216)
  - Name: 'लिज करारबोजिमको माल वस्तु नउठाउने र पुनः करारको आदेश' (Value: 166)
  - Name: 'लिलाम बदर' (Value: 18)
  - Name: 'लेनदेन' (Value: 19)
  - Name: 'वाटो निकास' (Value: 20)
  - Name: 'वाली मोही' (Value: 257)
  - Name: 'वाली विगो' (Value: 21)
  - Name: 'वाली सम्बन्धी' (Value: 256)
  - Name: 'विक्री सम्बन्धि' (Value: 250)
  - Name: 'वीमा' (Value: 22)
  - Name: 'वैना फिर्ता' (Value: 23)
  - Name: 'शेयर कायम गरिपाउँ' (Value: 389)
  - Name: 'शेयर सम्बन्धि' (Value: 390)
  - Name: 'शेषपछिको बकसपत्र' (Value: 144)
  - Name: 'सँधियार कायम गरी पाऊ' (Value: 194)
  - Name: 'संशोधन दाखिल खारेज' (Value: 252)
  - Name: 'सट्टापट्टा' (Value: 220)
  - Name: 'सन्धी सर्पन' (Value: 369)
  - Name: 'सफारी चलन' (Value: 240)
  - Name: 'समान जफत' (Value: 400)
  - Name: 'सम्पत्ति मसौट गरे भने' (Value: 392)
  - Name: 'सार्वजनिक जग्गा' (Value: 364)
  - Name: 'सार्वजनिक बाटो' (Value: 234)
  - Name: 'सावाँ ब्याज भराइपाउा' (Value: 394)
  - Name: 'सुन विदेश निकासी' (Value: 281)
  - Name: 'सेवाबाट अबकाश' (Value: 251)
  - Name: 'स्वीकृत किलोवाट कायम गरी हिसाब गराई पाउं' (Value: 412)
  - Name: 'हक कायम' (Value: 140)
  - Name: 'हक बेहक' (Value: 409)
  - Name: 'हकदार कायम' (Value: 328)
  - Name: 'हकसफा' (Value: 179)
  - Name: 'हद फुकाई पाउँ' (Value: 278)
  - Name: 'हदबन्दी' (Value: 223)
  - Name: 'हरण भएको जिमिदारी नम्बरी' (Value: 295)
  - Name: 'हरहिसाब गराइपाऊँ ।' (Value: 211)
  - Name: 'हर्जना दिलाई' (Value: 306)
  - Name: 'हाल आवादी' (Value: 327)
  - Name: 'हुण्डाबाली' (Value: 293)
  - Name: 'हेर्न नहुने मुद्दा हेर्‍यो' (Value: 289)
  - Name: '७ नं. फाँटवारी' (Value: 363)
  (Found 210 names)

--- Mudda Type: 'सरकारबादी देवानी' (Value: 2) ---
  - Name: 'गैरकानूनी सस्पेन्ड' (Value: 276)
  - Name: 'तलब दिलाई पाऊँ' (Value: 402)
  - Name: 'रकम असुल' (Value: 415)
  - Name: 'सरकारी सम्पत्ति' (Value: 24)
  (Found 4 names)

--- Mudda Type: 'दुनियावादी फौजदारी' (Value: 3) ---
  - Name: '.......' (Value: 386)
  - Name: 'अदल सम्बन्धी' (Value: 25)
  - Name: 'अदालतको अबहेलना' (Value: 26)
  - Name: 'ईलाज गर्ने' (Value: 27)
  - Name: 'उपभोक्ताको स्वास्थ्यमा प्रतिकूल असर' (Value: 424)
  - Name: 'करकाप' (Value: 28)
  - Name: 'करणी' (Value: 29)
  - Name: 'कीर्ते जालसाजी' (Value: 30)
  - Name: 'कुटपीट' (Value: 201)
  - Name: 'कुटपीट लुटपीट' (Value: 31)
  - Name: 'कोटाको कपडा' (Value: 375)
  - Name: 'गाली वेईज्जती' (Value: 32)
  - Name: 'गौचरन आवाद' (Value: 371)
  - Name: 'घरेलु हिंसा' (Value: 33)
  - Name: 'चेक अनादर' (Value: 34)
  - Name: 'चौपाया' (Value: 35)
  - Name: 'जारी' (Value: 36)
  - Name: 'जालसाज' (Value: 152)
  - Name: 'झुठ्ठा वकपत्र' (Value: 37)
  - Name: 'ठगी' (Value: 413)
  - Name: 'दुनियावादी फौजदारी विविध' (Value: 38)
  - Name: 'धनमाल करकाप' (Value: 310)
  - Name: 'नाताकायम' (Value: 39)
  - Name: 'बइजति' (Value: 356)
  - Name: 'बढी अन्न स्टक' (Value: 323)
  - Name: 'बिजाइ विद्युत' (Value: 378)
  - Name: 'बिहावारी' (Value: 40)
  - Name: 'बेइजति' (Value: 357)
  - Name: 'बौद्धिक सम्पत्ति सम्वन्धि' (Value: 41)
  - Name: 'यातना क्षतिपूर्ति' (Value: 42)
  - Name: 'लुटपिट' (Value: 176)
  - Name: 'लोग्ने कायम' (Value: 319)
  - Name: 'वाल श्रम' (Value: 43)
  - Name: 'विधुतीय कारोवार' (Value: 44)
  - Name: 'विवाह बदर' (Value: 227)
  - Name: 'सम्बन्ध विच्छेद' (Value: 45)
  - Name: 'साँध सिमाना' (Value: 370)
  (Found 37 names)

--- Mudda Type: 'सरकारवादी फौजदारी' (Value: 4) ---
  - Name: 'अङ्गभङ' (Value: 46)
  - Name: 'अदल' (Value: 47)
  - Name: 'अध्यागमन सम्बन्धि' (Value: 48)
  - Name: 'अनियमितरूपमा मदिरा सञ्चालन' (Value: 342)
  - Name: 'अपशब्द' (Value: 340)
  - Name: 'अपहरण/ बन्धक' (Value: 49)
  - Name: 'अपहेलना' (Value: 130)
  - Name: 'अपाङ' (Value: 50)
  - Name: 'अप्राकृतिक मैथुन' (Value: 421)
  - Name: 'अभिलेख' (Value: 51)
  - Name: 'अमानवीय व्यवहार' (Value: 432)
  - Name: 'अवैध पैठारी' (Value: 329)
  - Name: 'अवैधानिक संघ संस्था खोले खोलाए' (Value: 406)
  - Name: 'आगलागी' (Value: 52)
  - Name: 'आदेश' (Value: 334)
  - Name: 'आदेश बदर' (Value: 238)
  - Name: 'आमाको दुध प्रतिस्थापन' (Value: 53)
  - Name: 'आयकर' (Value: 233)
  - Name: 'आवश्यक पदार्थ संबन्धी' (Value: 54)
  - Name: 'आवश्यक वस्तु संबन्धी' (Value: 55)
  - Name: 'आवश्यक सेवा संबन्धी' (Value: 56)
  - Name: 'उपभोक्ता हित सम्बन्धी' (Value: 57)
  - Name: 'औषधि' (Value: 58)
  - Name: 'कम्प्यूटर सम्बन्धी अपराध' (Value: 59)
  - Name: 'कर सम्बन्धी' (Value: 157)
  - Name: 'करणी' (Value: 60)
  - Name: 'कर्तव्य ज्यान' (Value: 131)
  - Name: 'कर्तव्यज्यान' (Value: 135)
  - Name: 'कालो बजारी' (Value: 61)
  - Name: 'किर्ते' (Value: 160)
  - Name: 'क्षतिपूर्ति' (Value: 177)
  - Name: 'खाद्यन्न स्टक' (Value: 299)
  - Name: 'खाध्य सम्बन्धी' (Value: 62)
  - Name: 'खुन' (Value: 288)
  - Name: 'खोटा चलन' (Value: 63)
  - Name: 'गर्भ तुहाउने उद्योग' (Value: 292)
  - Name: 'गर्भपतन' (Value: 189)
  - Name: 'गुणस्तर' (Value: 64)
  - Name: 'गैडासम्बन्धी' (Value: 165)
  - Name: 'गैर कानूनी' (Value: 344)
  - Name: 'गैर सैनिक हवाई उडान' (Value: 65)
  - Name: 'गैरकानूनी कारवाही' (Value: 302)
  - Name: 'गैह्रकानूनी लाभ' (Value: 321)
  - Name: 'गोली हान्यो' (Value: 331)
  - Name: 'गोवध' (Value: 66)
  - Name: 'चन्दा / चिठ्ठा' (Value: 67)
  - Name: 'चलचित्र' (Value: 68)
  - Name: 'चाँदी निकासी' (Value: 395)
  - Name: 'चोरी' (Value: 69)
  - Name: 'चोरी निकासी' (Value: 360)
  - Name: 'छात्रवृति' (Value: 70)
  - Name: 'छापाखाना' (Value: 71)
  - Name: 'जग्गा प्राप्ति' (Value: 72)
  - Name: 'जडिबुटी' (Value: 73)
  - Name: 'जबर्जस्ती करणी' (Value: 137)
  - Name: 'जलश्रोत' (Value: 74)
  - Name: 'जातीय छुवाछूत' (Value: 158)
  - Name: 'जासुसी सम्वन्धी' (Value: 75)
  - Name: 'जीउमास्ने बेच्ने' (Value: 151)
  - Name: 'जीवनाशक विषादि' (Value: 76)
  - Name: 'जुवा' (Value: 77)
  - Name: 'ज्यान' (Value: 78)
  - Name: 'ज्यान डाँका' (Value: 184)
  - Name: 'ज्यान मार्ने उद्योग' (Value: 156)
  - Name: 'ज्येष्ठ नागरिक' (Value: 79)
  - Name: 'झुक्याई सही छाप' (Value: 333)
  - Name: 'ठगी' (Value: 80)
  - Name: 'डाँका' (Value: 214)
  - Name: 'डाँका खुन' (Value: 196)
  - Name: 'डाँका चोरी' (Value: 164)
  - Name: 'तहबिल मसौट' (Value: 367)
  - Name: 'थुनछेक' (Value: 284)
  - Name: 'थुनुवा / कैदी भागे भगाएको' (Value: 81)
  - Name: 'दुरसंचार' (Value: 82)
  - Name: 'दैवी प्रकोप' (Value: 83)
  - Name: 'धर्म परिवर्तन' (Value: 218)
  - Name: 'धर्मलोप' (Value: 301)
  - Name: 'धितोपत्र कारोवार' (Value: 84)
  - Name: 'नकबजनी चोरी' (Value: 132)
  - Name: 'नक्कली नोट' (Value: 422)
  - Name: 'नागरिकता' (Value: 85)
  - Name: 'निर्वाचन अपराध' (Value: 86)
  - Name: 'नोकरीबाट हटाइएको' (Value: 222)
  - Name: 'नोटरी पव्लिक' (Value: 87)
  - Name: 'पर्ती जग्गा नामसारी गरी भ्रष्टाचार गरेको' (Value: 142)
  - Name: 'पशु स्वास्थय' (Value: 88)
  - Name: 'प्रकाशनको प्रमाणपत्र रद्द गरेको सम्बन्धमा' (Value: 407)
  - Name: 'प्रतिलिपि अधिकार सम्वन्धी' (Value: 89)
  - Name: 'प्रतिस्पर्धा सम्वन्धी' (Value: 90)
  - Name: 'प्राचिन मुर्ती चोरी' (Value: 268)
  - Name: 'बहुविवाह' (Value: 153)
  - Name: 'बाल यौन दुराचार' (Value: 429)
  - Name: 'बालबालिका बिरुद्धको अपराध' (Value: 91)
  - Name: 'बालहत्या' (Value: 384)
  - Name: 'बिबाह' (Value: 92)
  - Name: 'बेरीतसँग थुने' (Value: 279)
  - Name: 'बैंकिंङ अपराध' (Value: 93)
  - Name: 'बोक्सीको आरोप' (Value: 431)
  - Name: 'भ्रष्टाचार' (Value: 94)
  - Name: 'मानब अङ्ग बेचबिखन' (Value: 95)
  - Name: 'मानब वेचविखन तथा ओसार पसार' (Value: 96)
  - Name: 'मुद्दा फिर्ता' (Value: 224)
  - Name: 'मुर्ती चोरी' (Value: 267)
  - Name: 'मूल्य अभिवृद्धि कर' (Value: 418)
  - Name: 'मोटर चोरी' (Value: 341)
  - Name: 'मौलिक हक हनन' (Value: 294)
  - Name: 'रक्तचन्दन ओसारपसार' (Value: 414)
  - Name: 'राजकाज अपराध' (Value: 235)
  - Name: 'राजनीतिक उद्देश्यले संघ संस्था खोलेको' (Value: 236)
  - Name: 'राजश्व सम्वन्धी' (Value: 97)
  - Name: 'राज्य उलट पुलट' (Value: 274)
  - Name: 'राज्य बिरुद्धको अपराध' (Value: 98)
  - Name: 'राष्ट्र वैंक' (Value: 99)
  - Name: 'राहदानी संबन्धी' (Value: 100)
  - Name: 'रिभ्यु गरी पाउँ' (Value: 287)
  - Name: 'रिसवत' (Value: 148)
  - Name: 'लागुऔषध' (Value: 101)
  - Name: 'लिखतको गोप्यता' (Value: 102)
  - Name: 'वन' (Value: 103)
  - Name: 'वन्यजन्तु' (Value: 104)
  - Name: 'वाक तथा प्रकाशन स्वतन्त्रता' (Value: 366)
  - Name: 'विदेशी बिनिमय' (Value: 105)
  - Name: 'विदेशी विनिमय' (Value: 106)
  - Name: 'विधुतिय कारोबार' (Value: 107)
  - Name: 'विध्वंसात्मक अपराध' (Value: 231)
  - Name: 'विभागीय कारवाही' (Value: 365)
  - Name: 'विरुवा संरक्षण' (Value: 108)
  - Name: 'विवाह' (Value: 109)
  - Name: 'विविध' (Value: 110)
  - Name: 'विष्फोटक पदार्थ' (Value: 111)
  - Name: 'वैदेशिक रोजगार' (Value: 112)
  - Name: 'वैदेशिक रोजगार' (Value: 113)
  - Name: 'वैदेशिक रोजगार' (Value: 134)
  - Name: 'व्यक्तिगत धटना' (Value: 114)
  - Name: 'शिक्षा' (Value: 115)
  - Name: 'सम्पत्ति सुद्धिकरण' (Value: 116)
  - Name: 'सरकारी कागज छाप दस्तखत कीर्ते' (Value: 117)
  - Name: 'सरकारी छाप दस्तखत कीर्ते' (Value: 147)
  - Name: 'सरकारी सेवा प्रवेश' (Value: 373)
  - Name: 'सरकारी हानी नोक्सानी' (Value: 372)
  - Name: 'सवारी गौवध' (Value: 225)
  - Name: 'सवारी ज्यान' (Value: 133)
  - Name: 'सही रास्ता पत्रिका बन्द गरे' (Value: 318)
  - Name: 'सामाजिक अपराध' (Value: 118)
  - Name: 'सार्वजनिक अपराध' (Value: 119)
  - Name: 'सेना सम्बन्धी' (Value: 120)
  - Name: 'स्वास्थ्य व्यवसायी' (Value: 121)
  - Name: 'हकदार कायम गरिपाउँ' (Value: 410)
  - Name: 'हतियार चलाई काटेको' (Value: 271)
  - Name: 'हाडनाता करणी' (Value: 242)
  - Name: 'हातहतियार खरखजाना' (Value: 122)
  - Name: 'हुलाक' (Value: 123)
  (Found 152 names)

--- Mudda Type: 'रिट' (Value: 5) ---
  - Name: '................' (Value: 348)
  - Name: 'अधिकारपृच्छा' (Value: 124)
  - Name: 'आज्ञा, आदेश वा पुर्जि जारी गरिपाऊँ' (Value: 355)
  - Name: 'उत्प्रेषण' (Value: 125)
  - Name: 'उत्प्रेषण / परमादेश' (Value: 428)
  - Name: 'खारेज ठाउँमा बसी काम गरे' (Value: 303)
  - Name: 'निषेधाज्ञा' (Value: 126)
  - Name: 'परमादेश' (Value: 127)
  - Name: 'प्रतिषेध' (Value: 128)
  - Name: 'बन्दीप्रत्यक्षीकरण' (Value: 129)
  - Name: 'विशेष रिट' (Value: 143)
  - Name: 'सरसियोररीको रिट जारी' (Value: 273)
  (Found 12 names)

--- Mudda Type: 'निवेदन' (Value: 6) ---
  - Name: '...........' (Value: 387)
  - Name: 'आदेश संशोधन गरी पाऊँ' (Value: 173)
  - Name: 'टिप्पणी आदेश' (Value: 187)
  - Name: 'दरपीठ आदेश बदर गरी पाउँ' (Value: 381)
  - Name: 'निवेदन दर्ता गरी पाऊँ' (Value: 197)
  - Name: 'निवेदन/प्रतिवेदन' (Value: 204)
  - Name: 'पुनरावलोकन गरी पाऊँ ।' (Value: 138)
  - Name: 'पुनरावेदन सरह मुद्दा हेरी पाउँ' (Value: 260)
  - Name: 'पुनरावेदनको अनुमति पाऊँ' (Value: 338)
  - Name: 'बेरितको आदेश बदर' (Value: 208)
  - Name: 'मुद्दा दोहोर्‍याई हेरी पाऊँ' (Value: 209)
  - Name: 'मुद्दा सकार गरिपाऊँ' (Value: 352)
  - Name: 'मुद्दाको अनुमति' (Value: 298)
  - Name: 'मृत्यु दर्ता प्रमाणपत्र बदर ।' (Value: 198)
  - Name: 'संविधानसँग बाझिएका कानूनी प्रावधान अमान्य र बदर' (Value: 219)
  (Found 15 names)

--- Mudda Type: 'विविध' (Value: 7) ---
  - Name: '...' (Value: 312)
  - Name: 'निर्देशन बदर' (Value: 416)
  - Name: 'माफी पाऊँ' (Value: 228)
  (Found 3 names)"""

mudda_mapping = parse_mudda_mapping(mapping_text)

print(mudda_mapping)

{'1': [{'value': '1', 'text': 'अंश'}, {'value': '314', 'text': 'अंश जालसाजी'}, {'value': '186', 'text': 'अंशबन्डा'}, {'value': '423', 'text': 'अग्नि बिमा दाबी'}, {'value': '433', 'text': 'अधिकार पत्र बदर'}, {'value': '426', 'text': 'अनियमितता'}, {'value': '2', 'text': 'अपुताली'}, {'value': '300', 'text': 'अपुताली धनमाल'}, {'value': '419', 'text': 'अबन्डा जग्गा बन्डा'}, {'value': '326', 'text': 'अबन्डा धन बन्डा गराई पाउँ'}, {'value': '404', 'text': 'अर्को लिखत गराइपाऊँ'}, {'value': '245', 'text': 'अवैध रूपमा भवन निर्माण'}, {'value': '172', 'text': 'आदेश जारी गरी पाऊँ'}, {'value': '207', 'text': 'आदेश बदर'}, {'value': '262', 'text': 'आदेश बदर गरी हाजिर गराई पाउँ'}, {'value': '265', 'text': 'आम्दानी खर्च'}, {'value': '305', 'text': 'आयस्ता दिलाई पाऊँ'}, {'value': '307', 'text': 'आयस्ता वाली'}, {'value': '286', 'text': 'आर्य समाजी'}, {'value': '205', 'text': 'इन्साफ जाँच'}, {'value': '391', 'text': 'उखडा जग्गा'}, {'value': '258', 'text': 'उपयुक्त आदेश जारी गरी पाउँ'}, {'value': '241', 'tex

In [57]:
# Thread-safe print function
def safe_print(message):
    with print_lock:
        print(message)


In [59]:
def initialize_thread_driver():
    """Initialize a new WebDriver instance for the thread"""
    options = webdriver.ChromeOptions()
    options.add_argument('--headless')
    options.add_argument('--no-sandbox')
    options.add_argument('--disable-dev-shm-usage')
    options.add_argument('--disable-gpu')
    options.add_argument('--disable-extensions')

    driver = webdriver.Chrome(options=options)
    driver.set_page_load_timeout(30)
    driver.implicitly_wait(10)

    return driver

In [61]:
def worker_thread(thread_id, max_pages=1000): # Default high max_pages
    """Worker thread function to process jobs from the queue with detailed logging."""
    safe_print(f"[Thread {thread_id}] Started.")
    driver = None # Initialize driver as None initially

    try: # Outer try to handle driver lifecycle
        try: # Inner try for initial driver setup
            driver = initialize_thread_driver()
            safe_print(f"[Thread {thread_id}] WebDriver initialized.")
        except Exception as e:
            safe_print(f"[Thread {thread_id}] CRITICAL: Failed to initialize WebDriver: {type(e).__name__} - {e}. Thread exiting.")
            return # Cannot proceed without a driver

        while True: # Main job processing loop
            job = None
            try:
                # Get a job from the queue (non-blocking)
                job = job_queue.get(block=False)
                mudda_type, mudda_name, mudda_name_text, faisala_type = job

                safe_print(f"[Thread {thread_id}] Processing job: MType={mudda_type}, MName='{mudda_name_text}' ({mudda_name}), FType={faisala_type}")

                # Process the job - Pass thread_id for logging within process_combination
                job_results = process_combination(driver, mudda_type, mudda_name, mudda_name_text, faisala_type, max_pages, thread_id)

                # Add results to results queue
                if job_results:
                    count = 0
                    for result in job_results:
                        results_queue.put(result)
                        count += 1
                    safe_print(f"[Thread {thread_id}] Job finished: Found {count} results for MType={mudda_type}, MName='{mudda_name_text}' ({mudda_name}), FType={faisala_type}")
                else:
                     safe_print(f"[Thread {thread_id}] Job finished: Found 0 results for MType={mudda_type}, MName='{mudda_name_text}' ({mudda_name}), FType={faisala_type}")

                # Mark job as done *after* successful processing
                job_queue.task_done()

            except queue.Empty:
                # No more jobs left in the queue
                safe_print(f"[Thread {thread_id}] Job queue empty. Exiting loop.")
                break # Exit the while loop

            except WebDriverException as e:
                safe_print(f"[Thread {thread_id}] WebDriverException encountered for job {job}: {type(e).__name__} - {e}. Attempting to reinitialize driver.")
                if job: job_queue.task_done() # Mark failed job done before attempting re-init
                try:
                    if driver: driver.quit()
                except Exception as quit_err:
                    safe_print(f"[Thread {thread_id}] Error quitting old driver: {quit_err}")
                try:
                    driver = initialize_thread_driver() # Re-assign driver variable
                    safe_print(f"[Thread {thread_id}] WebDriver reinitialized successfully.")
                except Exception as init_err:
                    safe_print(f"[Thread {thread_id}] CRITICAL: Failed to reinitialize WebDriver after error: {init_err}. Thread exiting loop.")
                    break # Exit loop if re-init fails

            except Exception as e:
                safe_print(f"[Thread {thread_id}] UNEXPECTED ERROR processing job {job}: {type(e).__name__} - {e}")
                # Log the traceback for unexpected errors
                import traceback
                safe_print(f"[Thread {thread_id}] Traceback:\n{traceback.format_exc()}")
                if job: job_queue.task_done() # Mark failed job done
                safe_print(f"[Thread {thread_id}] Skipping to next job attempt if available.")
                # Continue to the next iteration to try and get a new job

        # <<< End of while True loop >>>

    finally:
        # This block now executes *after* the while loop finishes or if an error occurs in the outer try
        if driver:
            try:
                driver.quit()
                safe_print(f"[Thread {thread_id}] WebDriver quit.")
            except Exception as e:
                safe_print(f"[Thread {thread_id}] Error quitting WebDriver on finish: {e}")
        safe_print(f"[Thread {thread_id}] Finished.")

In [83]:
def process_combination(driver, mudda_type, mudda_name, mudda_name_text, faisala_type, max_pages=1000, thread_id="N/A"):
    """
    Process a single combination with robust pagination, retries, specific 'no results' check,
    and handling for persistent page load failures by returning partial results.
    """
    results = []
    job_desc = f"MType={mudda_type}, MName='{mudda_name_text}' ({mudda_name}), FType={faisala_type}"
    safe_print(f"[Thread {thread_id}] Starting process_combination for {job_desc}")
    persistently_failed_page = None # Track if a page persistently failed

    try:
        # 1. Navigate to search page (Increased timeouts)
        safe_print(f"[Thread {thread_id}] Navigating to advance_search page...")
        driver.get("https://nkp.gov.np/advance_search")
        WebDriverWait(driver, 30).until(EC.presence_of_element_located((By.ID, "mudda_type")))
        safe_print(f"[Thread {thread_id}] Page loaded: {driver.title}")

        # Verify form presence
        try:
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.CSS_SELECTOR, "form.search-form")))
        except TimeoutException:
            safe_print(f"[Thread {thread_id}] Search form not found within timeout! Skipping job: {job_desc}")
            raise WebDriverException("Search form not found on page load.")

        # 2. Select mudda_type (Increased timeouts)
        try:
            mudda_type_select_element = WebDriverWait(driver, 15).until(
                EC.presence_of_element_located((By.ID, "mudda_type"))
            )
            mudda_type_select = Select(mudda_type_select_element)
            mudda_type_select.select_by_value(mudda_type)
            safe_print(f"[Thread {thread_id}] Selected mudda_type: {mudda_type}")
            WebDriverWait(driver, 20).until(
                EC.presence_of_element_located((By.XPATH, f"//select[@id='mudda_name']/option[@value='{mudda_name}']"))
            )
            safe_print(f"[Thread {thread_id}] Mudda_name dropdown updated.")
        except (NoSuchElementException, TimeoutException, UnexpectedTagNameException) as e:
            safe_print(f"[Thread {thread_id}] Error selecting mudda_type or waiting for mudda_name update: {type(e).__name__} - {e}. Skipping job: {job_desc}")
            return [] # Return empty results, cannot proceed

        # Get mudda_type text
        mudda_type_text = ""
        try:
            selected_option = mudda_type_select.first_selected_option
            mudda_type_text = selected_option.text
        except Exception as e:
            safe_print(f"[Thread {thread_id}] Warning: Could not get mudda_type_text: {e}")

        # 3. Select mudda_name (Increased timeouts)
        try:
            mudda_name_select_element = WebDriverWait(driver, 15).until(
                EC.element_to_be_clickable((By.ID, "mudda_name"))
            )
            mudda_name_select = Select(mudda_name_select_element)
            mudda_name_select.select_by_value(mudda_name)
            safe_print(f"[Thread {thread_id}] Selected mudda_name: {mudda_name}")
            time.sleep(0.5)
        except (NoSuchElementException, TimeoutException, UnexpectedTagNameException) as e:
            safe_print(f"[Thread {thread_id}] Error selecting mudda_name: {type(e).__name__} - {e}. Skipping job: {job_desc}")
            return []

        # 4. Set faisala_type using JavaScript
        try:
            js_script = f"""
            var el = document.getElementsByName('faisala_type')[0];
            if(el) {{ el.value = '{faisala_type}'; el.dispatchEvent(new Event('change', {{ bubbles: true }})); return true; }} else {{ return false; }}
            """
            if not driver.execute_script(js_script):
                safe_print(f"[Thread {thread_id}] Error setting faisala_type via JS: Element not found. Skipping job: {job_desc}")
                return []
            safe_print(f"[Thread {thread_id}] Set faisala_type: {faisala_type} via JS")
            time.sleep(0.5)
        except WebDriverException as e:
            safe_print(f"[Thread {thread_id}] Error executing JS for faisala_type: {e}. Skipping job: {job_desc}")
            return []

        # 5. Submit form (Increased timeouts)
        try:
            submit_button = WebDriverWait(driver, 15).until(
                EC.element_to_be_clickable((By.CSS_SELECTOR, "input[name='Submit'][type='submit']"))
            )
            submit_button.click()
            safe_print(f"[Thread {thread_id}] Form submitted.")
            # Wait for results page - Significantly longer wait
            WebDriverWait(driver, 60).until( # Increased initial results wait
                EC.presence_of_element_located((
                    By.XPATH,
                    "//article[contains(@class, 'format-standard')] | //div[@class='main-listing']/h2[contains(text(),'तपाईंको खोजको कुनै नतिजा फेला पारेन')] | //div[@id='pagination']"
                ))
            )
            safe_print(f"[Thread {thread_id}] Initial results page check passed.")
        except TimeoutException:
             safe_print(f"[Thread {thread_id}] Timeout waiting for initial results page after submit. Skipping job: {job_desc}")
             return []
        except (NoSuchElementException, ElementClickInterceptedException) as e:
            safe_print(f"[Thread {thread_id}] Error submitting form or waiting for results: {type(e).__name__} - {e}. Skipping job: {job_desc}")
            return []

        # 6. Process pages - Robust pagination loop
        current_page = 1
        NO_RESULTS_XPATH = "//div[@class='main-listing']/h2[contains(text(),'तपाईंको खोजको कुनै नतिजा फेला पारेन')]"
        MAX_ACTION_RETRIES = 3

        while current_page <= max_pages:
            safe_print(f"[Thread {thread_id}] --- Processing page {current_page} for {job_desc} ---")

            # A. Check for the specific "No results found" message
            try:
                driver.find_element(By.XPATH, NO_RESULTS_XPATH)
                safe_print(f"[Thread {thread_id}] Explicit 'No results found' message detected on page {current_page}. Stopping pagination.")
                break
            except NoSuchElementException:
                pass # Proceed
            except Exception as e:
                 safe_print(f"[Thread {thread_id}] Warning: Error checking for 'No results' message: {e}.")

            # B. Extract results
            page_results = []
            try:
                WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.XPATH, "//article[contains(@class, 'format-standard')] | //div[@id='pagination']"))) # Wait for articles or pagination
                page_results = extract_search_results(driver)
            except TimeoutException:
                safe_print(f"[Thread {thread_id}] Timeout waiting for articles/pagination on page {current_page}. Double checking 'No results' msg.")
                try:
                    driver.find_element(By.XPATH, NO_RESULTS_XPATH)
                    safe_print(f"[Thread {thread_id}] 'No results found' message detected after timeout. Stopping pagination.")
                except NoSuchElementException:
                    safe_print(f"[Thread {thread_id}] CRITICAL: No articles found and 'No results' message absent after timeout on page {current_page}. Stopping pagination for this job.")
                    persistently_failed_page = current_page # Mark the failure point
                break # Stop pagination on critical failure
            except Exception as e:
                safe_print(f"[Thread {thread_id}] Error during extract_search_results on page {current_page}: {type(e).__name__} - {e}. Stopping pagination for this job.")
                persistently_failed_page = current_page # Mark the failure point
                break

            # C. Process extracted results (if any)
            if page_results:
                safe_print(f"[Thread {thread_id}] Found {len(page_results)} results on page {current_page}")
                for result in page_results:
                    result["mudda_type_value"] = mudda_type
                    result["mudda_type_text"] = mudda_type_text
                    result["mudda_name_value"] = mudda_name
                    result["mudda_name_text"] = mudda_name_text
                    result["faisala_type_value"] = faisala_type
                    result["page"] = current_page
                    results.append(result)
            else:
                # No results extracted, but not the explicit "No results" page and no timeout above.
                safe_print(f"[Thread {thread_id}] No results extracted on page {current_page}, 'No results' message not found. Checking pagination link.")

            # D. Check if should continue
            if current_page >= max_pages:
                safe_print(f"[Thread {thread_id}] Reached max_pages limit ({max_pages}). Stopping pagination.")
                break

            if not has_next_page(driver):
                safe_print(f"[Thread {thread_id}] No 'next page' (») link found on page {current_page}. Stopping pagination.")
                break

            # E. Attempt navigation with retries
            safe_print(f"[Thread {thread_id}] Next page link found, attempting navigation from page {current_page}...")
            navigation_success = False
            for attempt in range(MAX_ACTION_RETRIES):
                if go_to_next_page(driver):
                    navigation_success = True
                    safe_print(f"[Thread {thread_id}] Navigation click successful (Attempt {attempt+1}/{MAX_ACTION_RETRIES}).")
                    break
                else:
                    safe_print(f"[Thread {thread_id}] Navigation click failed (Attempt {attempt+1}/{MAX_ACTION_RETRIES}). Retrying after pause...")
                    time.sleep(5 + attempt * 5)

            if not navigation_success:
                safe_print(f"[Thread {thread_id}] CRITICAL: Persistent failure navigating to next page after {MAX_ACTION_RETRIES} attempts. Stopping pagination for this job.")
                persistently_failed_page = current_page + 1 # Mark failure point as the page we couldn't reach
                break

            # F. Wait for NEW page content with retries --- MODIFIED FAILURE HANDLING ---
            current_page += 1
            content_loaded = False
            for attempt in range(MAX_ACTION_RETRIES):
                try:
                    # Wait for articles OR "no results" H2 OR pagination
                    WebDriverWait(driver, 75).until( # VERY LONG timeout for next page load
                        EC.presence_of_element_located((
                            By.XPATH,
                            "//article[contains(@class, 'format-standard')] | //div[@class='main-listing']/h2[contains(text(),'तपाईंको खोजको कुनै नतिजा फेला पारेन')] | //div[@id='pagination']"
                         ))
                    )
                    content_loaded = True
                    safe_print(f"[Thread {thread_id}] Page {current_page} content check passed (Attempt {attempt+1}/{MAX_ACTION_RETRIES}).")
                    break # Success!
                except TimeoutException:
                    safe_print(f"[Thread {thread_id}] Timeout waiting for page {current_page} content (Attempt {attempt+1}/{MAX_ACTION_RETRIES}). Retrying after pause...")
                    if attempt < MAX_ACTION_RETRIES - 1:
                        time.sleep(7 + attempt * 7) # Increasing pause
                        # Optional: Refresh before retrying wait
                        try:
                           safe_print(f"[Thread {thread_id}] Refreshing page {driver.current_url} before next wait attempt...")
                           driver.refresh()
                        except Exception as refresh_err:
                           safe_print(f"[Thread {thread_id}] Error during refresh: {refresh_err}")
                    # else: Last attempt failed

            if not content_loaded:
                # **** THIS IS THE KEY CHANGE ****
                safe_print(f"[Thread {thread_id}] CRITICAL: Persistent timeout waiting for content on page {current_page} after {MAX_ACTION_RETRIES} attempts. Stopping pagination for this job BUT returning partial results.")
                persistently_failed_page = current_page # Mark the failure point
                break # Exit the while loop, will return collected results

            # --- Loop continues ---

        # --- End of while loop ---

    except WebDriverException as e:
        safe_print(f"[Thread {thread_id}] WebDriverException in process_combination for {job_desc}: {type(e).__name__} - {e}. Raising to worker.")
        raise # Re-raise to trigger driver re-init in worker_thread
    except Exception as e:
        safe_print(f"[Thread {thread_id}] UNEXPECTED Error processing combination {job_desc}: {type(e).__name__} - {e}")
        import traceback
        safe_print(f"[Thread {thread_id}] Traceback:\n{traceback.format_exc()}")

    # Log final status for this combination
    if persistently_failed_page:
         safe_print(f"[Thread {thread_id}] Finished process_combination for {job_desc} PARTIALLY. Failed permanently at page {persistently_failed_page}. Returning {len(results)} results collected before failure.")
    else:
         safe_print(f"[Thread {thread_id}] Finished process_combination for {job_desc} successfully. Returning {len(results)} total results.")

    return results # Return whatever was collected

In [85]:


# Queue to store jobs (combinations to scrape)
job_queue = queue.Queue()

# Queue to store results from all threads
results_queue = queue.Queue()

# Lock for thread-safe printing
print_lock = threading.Lock()

# Global driver variable
driver = None

In [87]:
def run_full_scrape(mudda_type="1", num_threads=10):
    """Run a full scrape with enhanced logging, error handling, and periodic saving."""
    print(f"\n=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE {mudda_type} with {num_threads} threads ===\n")

    # --- Queue Clearing ---
    print("Clearing previous job and result queues...")
    cleared_jobs, cleared_results = 0, 0
    while not job_queue.empty():
        try:
            job_queue.get_nowait()
            job_queue.task_done()
            cleared_jobs += 1
        except queue.Empty:
            break
    while not results_queue.empty():
        try:
            results_queue.get_nowait()
            cleared_results += 1
        except queue.Empty:
            break
    print(f"Cleared {cleared_jobs} jobs and {cleared_results} results from previous runs.")

    # --- Job Preparation ---
    if mudda_type not in mudda_mapping:
        print(f"ERROR: No mapping found for mudda_type {mudda_type}. Exiting.")
        return []

    mudda_names = mudda_mapping[mudda_type]
    print(f"Found {len(mudda_names)} mudda_names for mudda_type {mudda_type}.")

    faisala_types = ["1", "2", "4", "5", "6", "7", "8", "9", "10", "11", "12",
                     "13", "14", "15", "16", "17", "18"]
    print(f"Using {len(faisala_types)} faisala_types.")

    total_combinations = len(mudda_names) * len(faisala_types)
    print(f"Total combinations to scrape: {total_combinations}")

    if total_combinations == 0:
        print("No combinations to scrape. Exiting.")
        return []

    # Add jobs to queue
    print("Adding jobs to the queue...")
    for mudda_name_info in mudda_names:
        for faisala_type in faisala_types:
            job_queue.put((mudda_type, mudda_name_info['value'], mudda_name_info['text'], faisala_type))
    print(f"Added {job_queue.qsize()} jobs to the queue.")

    # --- Threading Setup ---
    start_time = time.time()
    results_lock = threading.Lock() # Lock for accessing all_results list
    all_results = []
    save_interval_results = 500 # Save every N results collected
    save_interval_jobs = 100   # Or every N jobs completed
    last_save_count_results = 0
    last_save_count_jobs = 0
    total_jobs_initial = job_queue.qsize()
    completed_jobs = 0

    print(f"\nStarting {num_threads} worker threads...")
    threads = []
    for i in range(num_threads):
        # Pass the high max_pages value to each thread
        t = threading.Thread(target=worker_thread, args=(i, 1000)) # 1000 max pages per combo
        t.daemon = True # Allow main thread to exit even if workers are blocked
        t.start()
        threads.append(t)
    print("Worker threads started.")

    # --- Monitoring and Saving Loop ---
    print("\n--- Starting Scrape Monitoring ---")
    monitoring_interval = 15 # Check progress every 15 seconds
    try:
        while completed_jobs < total_jobs_initial:
            # Check if any worker thread has died unexpectedly
            active_threads = sum(1 for t in threads if t.is_alive())
            if active_threads < len(threads):
                 print(f"WARNING: {len(threads) - active_threads} worker thread(s) seem to have terminated unexpectedly.")
                 # Decide whether to continue or stop if threads die

            # Calculate progress based on job_queue tasks remaining
            # job_queue.qsize() can be approximate, task_done is more reliable
            # Let's estimate completed based on initial vs current qsize (less accurate but simple)
            current_qsize = job_queue.qsize()
            # Use job_queue.unfinished_tasks for a potentially more accurate count of active/pending tasks
            unfinished_tasks = job_queue.unfinished_tasks
            # Make sure completed_jobs doesn't exceed total
            completed_jobs = max(0, total_jobs_initial - unfinished_tasks)


            progress = (completed_jobs / total_jobs_initial) * 100 if total_jobs_initial > 0 else 100
            elapsed = time.time() - start_time

            # Estimate time remaining
            eta_str = "N/A"
            if completed_jobs > 0 and progress < 100:
                avg_time_per_job = elapsed / completed_jobs
                remaining_jobs = total_jobs_initial - completed_jobs
                remaining_time = avg_time_per_job * remaining_jobs
                eta_str = f"{remaining_time / 60:.1f} mins"

            # Collect results from queue
            current_results_batch = []
            while not results_queue.empty():
                try:
                    result = results_queue.get_nowait()
                    current_results_batch.append(result)
                except queue.Empty:
                    break

            new_results_count = len(current_results_batch)
            if new_results_count > 0:
                with results_lock:
                    all_results.extend(current_results_batch)
                print(f"Collected {new_results_count} new results. Total results: {len(all_results)}")

            # Print progress update
            print(f"Progress: {progress:.1f}% ({completed_jobs}/{total_jobs_initial}) | QSize: {current_qsize} | Unfinished: {unfinished_tasks} | Found: {len(all_results)} | Elapsed: {elapsed/60:.1f}m | ETA: {eta_str}")


            # --- Incremental Saving Logic ---
            save_triggered = False
            # Save based on number of results collected
            if len(all_results) >= last_save_count_results + save_interval_results:
                print(f"\nSaving incrementally based on result count ({len(all_results)} >= {last_save_count_results} + {save_interval_results})...")
                save_triggered = True
                last_save_count_results = len(all_results) # Update counter

            # Save based on number of jobs completed
            elif completed_jobs >= last_save_count_jobs + save_interval_jobs:
                 print(f"\nSaving incrementally based on job count ({completed_jobs} >= {last_save_count_jobs} + {save_interval_jobs})...")
                 save_triggered = True
                 last_save_count_jobs = completed_jobs # Update counter

            if save_triggered:
                incremental_filename = f"nepal_law_type{mudda_type}_incremental_{len(all_results)}r_{completed_jobs}j.csv"
                try:
                    with results_lock: # Ensure no modification during save
                        save_to_csv(list(all_results), incremental_filename) # Pass a copy
                    print(f"Incremental save successful: {len(all_results)} results saved to {incremental_filename}\n")
                except Exception as save_err:
                    print(f"ERROR during incremental save: {save_err}\n")


            # Check if all jobs are marked as done
            if unfinished_tasks == 0 and current_qsize == 0:
                 print("All jobs processed based on unfinished_tasks count.")
                 break # Exit monitoring loop

            # Wait before next check
            time.sleep(monitoring_interval)

        print("\n--- Monitoring loop finished. ---")

    except KeyboardInterrupt:
        print("\n--- KeyboardInterrupt detected! Stopping threads and saving results... ---")
        # Signal threads to stop (though they check queue.Empty) - not strictly needed with daemon threads
        # Wait a short time for threads to potentially finish current task
        time.sleep(5)
    except Exception as e:
        print(f"\n--- UNEXPECTED ERROR in main monitoring loop: {type(e).__name__} - {e} ---")
        import traceback
        print(f"Traceback:\n{traceback.format_exc()}")
        print("Attempting to save results anyway...")

    finally:
        print("\n--- Starting Final Cleanup ---")
        # Ensure all threads have finished (or give them time)
        # Note: With daemon threads, they might be abruptly stopped if main exits.
        # Proper shutdown would involve signaling threads via a shared flag or queue sentinel.
        # However, for simplicity here, we rely on them finishing via queue.Empty.
        print("Waiting briefly for threads to finish...")
        # job_queue.join() # This would wait until all task_done() calls are made

        # Collect any remaining results put in the queue after the last check
        print("Collecting final results from queue...")
        final_batch = []
        while not results_queue.empty():
            try:
                result = results_queue.get_nowait()
                final_batch.append(result)
            except queue.Empty:
                break
        if final_batch:
             with results_lock:
                all_results.extend(final_batch)
             print(f"Collected {len(final_batch)} final results. Total results: {len(all_results)}")


        # --- Final Statistics and Save ---
        end_time = time.time()
        total_time_minutes = (end_time - start_time) / 60
        final_completed_jobs = max(0, total_jobs_initial - job_queue.unfinished_tasks) # Recalculate completion

        print("\n--- Scrape Summary ---")
        print(f"Total execution time: {total_time_minutes:.2f} minutes.")
        print(f"Initial jobs: {total_jobs_initial}")
        print(f"Completed jobs (estimated): {final_completed_jobs}")
        print(f"Total results found: {len(all_results)}")

        if all_results:
            final_filename = f"nepal_law_type{mudda_type}_full_{len(all_results)}r_{final_completed_jobs}j.csv"
            print(f"\nSaving final results to {final_filename}...")
            try:
                # No need for lock now as threads should be done
                save_to_csv(all_results, final_filename)
                print(f"Successfully saved {len(all_results)} results.")
            except Exception as save_err:
                print(f"ERROR during final save: {save_err}")
        else:
            print("\nNo results collected to save.")

        print("\n=== SCRAPING PROCESS FINISHED ===\n")
        return all_results # Return the collected data

In [89]:
full_results = run_full_scrape(mudda_type="5", num_threads=10)


=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE 5 with 10 threads ===

Clearing previous job and result queues...
Cleared 0 jobs and 0 results from previous runs.
Found 12 mudda_names for mudda_type 5.
Using 17 faisala_types.
Total combinations to scrape: 204
Adding jobs to the queue...
Added 204 jobs to the queue.

Starting 10 worker threads...
[Thread 0] Started.
[Thread 1] Started.
[Thread 2] Started.
[Thread 3] Started.
[Thread 4] Started.
[Thread 5] Started.
[Thread 6] Started.
[Thread 7] Started.
[Thread 8] Started.
[Thread 9] Started.
Worker threads started.

--- Starting Scrape Monitoring ---
Progress: 0.0% (0/204) | QSize: 204 | Unfinished: 204 | Found: 0 | Elapsed: 0.0m | ETA: N/A
[Thread 7] WebDriver initialized.
[Thread 7] Processing job: MType=5, MName='................' (348), FType=1
[Thread 7] Starting process_combination for MType=5, MName='................' (348), FType=1
[Thread 7] Navigating to advance_search page...
[Thread 8] WebDriver initialized.
[Thread 8] Process

In [ ]:
full_results = run_full_scrape(mudda_type="6", num_threads=10)

In [ ]:
full_results = run_full_scrape(mudda_type="7", num_threads=10)

In [ ]:
full_results = run_full_scrape(mudda_type="5", num_threads=10)

In [90]:
full_results = run_full_scrape(mudda_type="1", num_threads=10)


=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE 1 with 10 threads ===

Clearing previous job and result queues...
Cleared 0 jobs and 0 results from previous runs.
Found 209 mudda_names for mudda_type 1.
Using 17 faisala_types.
Total combinations to scrape: 3553
Adding jobs to the queue...
Added 3553 jobs to the queue.

Starting 10 worker threads...
[Thread 0] Started.
[Thread 1] Started.
[Thread 2] Started.
[Thread 3] Started.
[Thread 4] Started.
[Thread 5] Started.
[Thread 6] Started.
[Thread 7] Started.
[Thread 8] Started.
[Thread 9] Started.
Worker threads started.

--- Starting Scrape Monitoring ---
Progress: 0.0% (0/3553) | QSize: 3553 | Unfinished: 3553 | Found: 0 | Elapsed: 0.0m | ETA: N/A
[Thread 5] WebDriver initialized.
[Thread 3] WebDriver initialized.
[Thread 3] Processing job: MType=1, MName='अंश' (1), FType=2
[Thread 3] Starting process_combination for MType=1, MName='अंश' (1), FType=2
[Thread 3] Navigating to advance_search page...
[Thread 9] WebDriver initialized.
[Thread 

In [93]:
full_results = run_full_scrape(mudda_type="2", num_threads=10)


=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE 2 with 10 threads ===

Clearing previous job and result queues...
Cleared 0 jobs and 0 results from previous runs.
Found 4 mudda_names for mudda_type 2.
Using 17 faisala_types.
Total combinations to scrape: 68
Adding jobs to the queue...
Added 68 jobs to the queue.

Starting 10 worker threads...
[Thread 0] Started.
[Thread 1] Started.
[Thread 2] Started.
[Thread 3] Started.
[Thread 4] Started.
[Thread 5] Started.
[Thread 6] Started.
[Thread 7] Started.
[Thread 8] Started.
[Thread 9] Started.
Worker threads started.

--- Starting Scrape Monitoring ---
Progress: 0.0% (0/68) | QSize: 68 | Unfinished: 68 | Found: 0 | Elapsed: 0.0m | ETA: N/A
[Thread 9] WebDriver initialized.
[Thread 9] Processing job: MType=2, MName='गैरकानूनी सस्पेन्ड' (276), FType=1
[Thread 9] Starting process_combination for MType=2, MName='गैरकानूनी सस्पेन्ड' (276), FType=1
[Thread 9] Navigating to advance_search page...
[Thread 0] WebDriver initialized.
[Thread 0] Processin

In [95]:
full_results = run_full_scrape(mudda_type="3", num_threads=10)


=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE 3 with 10 threads ===

Clearing previous job and result queues...
Cleared 0 jobs and 0 results from previous runs.
Found 37 mudda_names for mudda_type 3.
Using 17 faisala_types.
Total combinations to scrape: 629
Adding jobs to the queue...
Added 629 jobs to the queue.

Starting 10 worker threads...
[Thread 0] Started.
[Thread 1] Started.
[Thread 2] Started.
[Thread 3] Started.
[Thread 4] Started.
[Thread 5] Started.
[Thread 6] Started.
[Thread 7] Started.
[Thread 8] Started.
[Thread 9] Started.
Worker threads started.

--- Starting Scrape Monitoring ---
Progress: 0.0% (0/629) | QSize: 629 | Unfinished: 629 | Found: 0 | Elapsed: 0.0m | ETA: N/A
[Thread 4] WebDriver initialized.
[Thread 4] Processing job: MType=3, MName='.......' (386), FType=1
[Thread 4] Starting process_combination for MType=3, MName='.......' (386), FType=1
[Thread 4] Navigating to advance_search page...
[Thread 8] WebDriver initialized.
[Thread 8] Processing job: MType=3, 

In [97]:
full_results = run_full_scrape(mudda_type="6", num_threads=10)


=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE 6 with 10 threads ===

Clearing previous job and result queues...
Cleared 0 jobs and 0 results from previous runs.
Found 15 mudda_names for mudda_type 6.
Using 17 faisala_types.
Total combinations to scrape: 255
Adding jobs to the queue...
Added 255 jobs to the queue.

Starting 10 worker threads...
[Thread 0] Started.
[Thread 1] Started.
[Thread 2] Started.
[Thread 3] Started.
[Thread 4] Started.
[Thread 5] Started.
[Thread 6] Started.
[Thread 7] Started.
[Thread 8] Started.
[Thread 9] Started.
Worker threads started.

--- Starting Scrape Monitoring ---
Progress: 0.0% (0/255) | QSize: 255 | Unfinished: 255 | Found: 0 | Elapsed: 0.0m | ETA: N/A
[Thread 9] WebDriver initialized.
[Thread 9] Processing job: MType=6, MName='...........' (387), FType=1
[Thread 9] Starting process_combination for MType=6, MName='...........' (387), FType=1
[Thread 9] Navigating to advance_search page...
[Thread 8] WebDriver initialized.
[Thread 8] Processing job: M

In [98]:
full_results = run_full_scrape(mudda_type="7", num_threads=10)


=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE 7 with 10 threads ===

Clearing previous job and result queues...
Cleared 0 jobs and 0 results from previous runs.
Found 3 mudda_names for mudda_type 7.
Using 17 faisala_types.
Total combinations to scrape: 51
Adding jobs to the queue...
Added 51 jobs to the queue.

Starting 10 worker threads...
[Thread 0] Started.
[Thread 1] Started.
[Thread 2] Started.
[Thread 3] Started.
[Thread 4] Started.
[Thread 5] Started.
[Thread 6] Started.
[Thread 7] Started.
[Thread 8] Started.
[Thread 9] Started.
Worker threads started.

--- Starting Scrape Monitoring ---
Progress: 0.0% (0/51) | QSize: 51 | Unfinished: 51 | Found: 0 | Elapsed: 0.0m | ETA: N/A
[Thread 9] WebDriver initialized.
[Thread 9] Processing job: MType=7, MName='...' (312), FType=1
[Thread 9] Starting process_combination for MType=7, MName='...' (312), FType=1
[Thread 9] Navigating to advance_search page...
[Thread 8] WebDriver initialized.
[Thread 8] Processing job: MType=7, MName='...' (3

In [101]:
full_results = run_full_scrape(mudda_type="4", num_threads=10)


=== INITIALIZING FULL SCRAPE FOR MUDDA_TYPE 4 with 10 threads ===

Clearing previous job and result queues...
Cleared 0 jobs and 0 results from previous runs.
Found 152 mudda_names for mudda_type 4.
Using 17 faisala_types.
Total combinations to scrape: 2584
Adding jobs to the queue...
Added 2584 jobs to the queue.

Starting 10 worker threads...
[Thread 0] Started.
[Thread 1] Started.
[Thread 2] Started.
[Thread 3] Started.
[Thread 4] Started.
[Thread 5] Started.
[Thread 6] Started.
[Thread 7] Started.
[Thread 8] Started.
[Thread 9] Started.
Worker threads started.

--- Starting Scrape Monitoring ---
Progress: 0.0% (0/2584) | QSize: 2584 | Unfinished: 2584 | Found: 0 | Elapsed: 0.0m | ETA: N/A
[Thread 9] WebDriver initialized.
[Thread 9] Processing job: MType=4, MName='अङ्गभङ' (46), FType=1
[Thread 9] Starting process_combination for MType=4, MName='अङ्गभङ' (46), FType=1
[Thread 9] Navigating to advance_search page...
[Thread 3] WebDriver initialized.
[Thread 3] Processing job: MType=4

Error sending stats to Plausible: error sending request for url (https://plausible.io/api/event)


Progress: 21.3% (551/2584) | QSize: 2027 | Unfinished: 2033 | Found: 756 | Elapsed: 34.3m | ETA: 126.4 mins
[Thread 8] WebDriver reinitialized successfully.
[Thread 8] Processing job: MType=4, MName='खाध्य सम्बन्धी' (62), FType=15
[Thread 8] Starting process_combination for MType=4, MName='खाध्य सम्बन्धी' (62), FType=15
[Thread 8] Navigating to advance_search page...
[Thread 3] WebDriver reinitialized successfully.
[Thread 3] Processing job: MType=4, MName='खाध्य सम्बन्धी' (62), FType=16
[Thread 3] Starting process_combination for MType=4, MName='खाध्य सम्बन्धी' (62), FType=16
[Thread 3] Navigating to advance_search page...
[Thread 9] WebDriver reinitialized successfully.
[Thread 9] Processing job: MType=4, MName='खाध्य सम्बन्धी' (62), FType=17
[Thread 9] Starting process_combination for MType=4, MName='खाध्य सम्बन्धी' (62), FType=17
[Thread 9] Navigating to advance_search page...
[Thread 7] WebDriver reinitialized successfully.
[Thread 7] Processing job: MType=4, MName='खाध्य सम्बन्धी